In [1]:
# Tang Kit Lim (WQD190032)

import json
import re
import sys
import requests
import datetime
import traceback
import pandas as pd
from pathlib import Path

## Crawling Township & Transaction Data from Edgeprop

In [2]:
# general function used in web crawling  

def format_url(input_string):
    if input_string is None:
        return 'null'
    return input_string.replace(' ', '%20').strip()


def format_slug(input_string):
    if input_string is None:
        return 'null'
    return re.sub(r'\W+', '-', input_string.strip().lower())

In [3]:
# directories to store newly crawled data
data_directory = '../data/'
township_data_directory = data_directory + 'new/edgeprop/townships/'
transaction_data_directory = data_directory + 'new/edgeprop/transactions/'
poi_data_directory = data_directory + 'new/iproperty/poi/'
Path(township_data_directory).mkdir(parents=True, exist_ok=True)
Path(transaction_data_directory).mkdir(parents=True, exist_ok=True)
Path(poi_data_directory).mkdir(parents=True, exist_ok=True)
coordinates = list()
max_crawl_retry = 5

In [4]:
# General crawler function for Edge Prop

def edgeprop_crawler(url):
    headers = {
        'user-agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/80.0.3987.149 '
                      'Safari/537.36 '
    }

    retry_count = 0
    while True:
        retry_count = retry_count + 1
        if retry_count >= max_crawl_retry:
            return None

        try:
            request = requests.get(url, headers=headers, timeout=60)
            request.raise_for_status()
            response = request.json()
        except requests.exceptions.HTTPError as errh:
            print('Http Error:', str(errh), '[Retry ' + str(retry_count) + ']')
            continue
        except requests.exceptions.ConnectionError as errc:
            print('Error Connecting:', str(errc), '[Retry ' + str(retry_count) + ']')
            continue
        except requests.exceptions.Timeout as errt:
            print('Timeout Error:', str(errt), '[Retry ' + str(retry_count) + ']')
            continue
        except requests.exceptions.RequestException as err:
            print('Unknown Error:', str(err), '[Retry ' + str(retry_count) + ']')
            continue
        except ValueError as jerr:
            print('Json Error:', str(jerr), '[Retry ' + str(retry_count) + ']')
            continue
        else:
            return response


In [5]:
# some variables holding information related to the url/parameter to crawl
api_url = 'https://www.edgeprop.my/jwdalice/api/v1/transactions/'
townships_url_template = api_url + 'search?&category=RESIDENTIAL&state={}&datefrom={}&dateto={}&page={}&respp=10&key='
transactions_url_template = api_url + 'details?&category=RESIDENTIAL&state={}&area={}&datefrom={}&dateto={}&project={}&page={}&key='

states = [
    'JOHOR', 'KEDAH', 'KELANTAN', 'KUALA LUMPUR', 'LABUAN', 'MELAKA', 'NEGERI SEMBILAN', 'PAHANG',
    'PENANG', 'PERAK', 'PERLIS', 'PUTRAJAYA', 'SABAH', 'SARAWAK', 'SELANGOR', 'TERENGGANU'
]


In [6]:
start_time = datetime.datetime.now()
print('Starts:', start_time)

# for all states in list
for state in states:
    page = 1
    date_from = '2017-01-01'
    date_to = '2019-12-31'

    retry_count = 0
    township_count = 1
    print('State:', state)
    
    while True:
        # crawl the townships list for the current state
        townships_url = townships_url_template.format(format_url(state), date_from, date_to, str(page))
        print(' Page', page, ':', townships_url)

        township_list = edgeprop_crawler(townships_url)

        if township_list is None:
            print('  Error Requesting Page:', townships_url)
            print('  Try next page')

            page = page + 1
            retry_count = retry_count + 1
            if retry_count >= max_crawl_retry:
                print('  Tried', retry_count, 'pages. Skipped to next state.')
                break

            continue

        retry_count = 0
        total_pages = township_list['totalpages']
        total_townships = township_list['total']
        townships = township_list['property']

        if page == 1:
            print('  Total Townships:', total_townships)
            print('  Total Pages:', total_pages)

        if page > int(total_pages):
            break

        print('   Page', page, 'of', total_pages)

        # Write townships to files
        with open(
            township_data_directory + format_slug(state) + '_' + date_from + '_' + date_to + '_' +
            str(page) + '_' + 'of' + '_' + str(total_pages) + '.json', 'w'
        ) as json_file:
            json.dump(townships, json_file)

        
        # for each township in current township list
        for township in townships:

            area = township['area']
            transaction_date_from = date_from
            transaction_date_to = date_to
            project = township['project_name']
            asset_id = township['asset_id']
            latitude = township['lat']
            longitude = township['lon']
            filed_transaction_count = township['fieldtransactions']
            transaction_page = 1

            print('    ' + str(township_count) + '.', 'Township:', project,
                  '- Estimated', filed_transaction_count, 'Transactions')
            
            if int(filed_transaction_count) > 0:
                retry_count = 0
                crawled_transaction_count = 0
                crawled_page_count = 0

                # to be used by POI crawler later
                coordinates.append({
                    "latitude": str(latitude),
                    "longitude": str(longitude)
                })

                # crawl transactions for current township
                # each API call for public without account return last 10 transactions only
                # need to crawl page by page, bu adjusting from latest date to older date
                while True:
                    transactions_url = transactions_url_template.format(
                        format_url(state), format_url(area), transaction_date_from, transaction_date_to,
                        format_url(project), str(transaction_page)
                    )

                    print('     Date To:', transaction_date_to, ':', transactions_url)

                    transaction_list = edgeprop_crawler(transactions_url)
                    if transaction_list is None:
                        print('      Error Requesting Page:', transactions_url)

                        retry_count = retry_count + 1
                        if retry_count >= max_crawl_retry:
                            print('      Tried', retry_count, 'times. Skipped to next township.')
                            break

                        continue

                    retry_count = 0
                    total_transaction_pages = transaction_list['totalpages']
                    transactions = transaction_list['property']

                    if len(transactions) == 0:
                        break

                    oldest_transaction = transactions[-1]

                    crawled_transaction_count = crawled_transaction_count + len(transactions)
                    crawled_page_count = crawled_page_count + 1

                    print('      Crawled', crawled_page_count,
                          'pages with', crawled_transaction_count, 'transactions')

                    # write transactions to files
                    with open(
                            transaction_data_directory + str(asset_id) + '_' + format_slug(project) + '_' +
                            transaction_date_to + '_' + str(crawled_transaction_count) + '.json', 'w'
                    ) as json_file:
                        json.dump(transactions, json_file)

                    if total_transaction_pages == 1:
                        break

                    # adjust the period end date to the oldest transaction crawled
                    # so that we can crawl backward, until the start date.
                    date_from_unixtimestamp = datetime.datetime.strptime(transaction_date_from, '%Y-%m-%d')
                    previous_date_to_unixtimestamp = datetime.datetime.strptime(transaction_date_to, '%Y-%m-%d')
                    new_date_to_unixtimestamp = datetime.datetime.utcfromtimestamp(oldest_transaction['date'])

                    if previous_date_to_unixtimestamp == new_date_to_unixtimestamp:
                        if date_from_unixtimestamp == new_date_to_unixtimestamp:
                            break
                        else:
                            new_date_to_unixtimestamp = new_date_to_unixtimestamp - datetime.timedelta(days = 1)

                    transaction_date_to = new_date_to_unixtimestamp.strftime('%Y-%m-%d')

            township_count = township_count + 1

        page = page + 1
        
end_time = datetime.datetime.now()
print('Ends:', end_time)
print('Time Elapsed:', str(end_time - start_time))

Starts: 2020-06-10 02:12:35.504227
State: JOHOR
 Page 1 : https://www.edgeprop.my/jwdalice/api/v1/transactions/search?&category=RESIDENTIAL&state=JOHOR&datefrom=2017-01-01&dateto=2019-12-31&page=1&respp=10&key=
  Total Townships: 1504
  Total Pages: 151
   Page 1 of 151
    1. Township: Bandar Putra IOI - Estimated 1136 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2019-12-31&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 1 pages with 10 transactions
     Date To: 2019-10-24 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2019-10-24&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 2 pages with 20 transactions
     Date To: 2019-10-07 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01

      Crawled 31 pages with 310 transactions
     Date To: 2018-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-12-31&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 32 pages with 320 transactions
     Date To: 2018-12-29 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-12-29&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 33 pages with 330 transactions
     Date To: 2018-12-24 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-12-24&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 34 pages with 340 transactions
     Date To: 2018-12-14 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-12-14&proje

      Crawled 63 pages with 630 transactions
     Date To: 2018-05-22 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-05-22&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 64 pages with 640 transactions
     Date To: 2018-05-15 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-05-15&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 65 pages with 650 transactions
     Date To: 2018-05-07 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-05-07&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 66 pages with 660 transactions
     Date To: 2018-04-26 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2018-04-26&proje

      Crawled 95 pages with 950 transactions
     Date To: 2017-09-25 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-09-25&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 96 pages with 960 transactions
     Date To: 2017-09-19 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-09-19&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 97 pages with 970 transactions
     Date To: 2017-09-14 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-09-14&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 98 pages with 980 transactions
     Date To: 2017-09-11 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-09-11&proje

      Crawled 127 pages with 1270 transactions
     Date To: 2017-03-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-03-31&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 128 pages with 1280 transactions
     Date To: 2017-03-27 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-03-27&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 129 pages with 1290 transactions
     Date To: 2017-03-17 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-03-17&project=Bandar%20Putra%20IOI&page=1&key=
      Crawled 130 pages with 1300 transactions
     Date To: 2017-03-13 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=JOHOR&area=Segamat&datefrom=2017-01-01&dateto=2017-03-

...

      Crawled 1 pages with 1 transactions
    3057. Township: Taman Aur - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Klang&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Aur&page=1&key=
      Crawled 1 pages with 1 transactions
    3058. Township: Taman Bahagia - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Klang&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Bahagia&page=1&key=
      Crawled 1 pages with 10 transactions
     Date To: 2018-01-15 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Klang&datefrom=2017-01-01&dateto=2018-01-15&project=Taman%20Bahagia&page=1&key=
      Crawled 2 pages with 19 transactions
    3059. Township: Taman Batu Untung - Estimated 1 Transactions
     Date To: 2019-12

      Crawled 1 pages with 1 transactions
    3080. Township: Taman Desa Pelangi - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Hulu%20Langat&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Desa%20Pelangi&page=1&key=
      Crawled 1 pages with 1 transactions
 Page 309 : https://www.edgeprop.my/jwdalice/api/v1/transactions/search?&category=RESIDENTIAL&state=SELANGOR&datefrom=2017-01-01&dateto=2019-12-31&page=309&respp=10&key=
   Page 309 of 317
    3081. Township: Taman Desa Sinaran - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Dengkil&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Desa%20Sinaran&page=1&key=
      Crawled 1 pages with 1 transactions
    3082. Township: Taman Emas, Hulu Yam - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.ed

      Crawled 1 pages with 1 transactions
    3105. Township: Taman Meru Harapan 3 - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Klang&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Meru%20Harapan%203&page=1&key=
      Crawled 1 pages with 1 transactions
    3106. Township: Taman Meru Mulia - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Kapar&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Meru%20Mulia&page=1&key=
      Crawled 1 pages with 1 transactions
    3107. Township: Taman Meru Ria 2 - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Kapar&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Meru%20Ria%202&page=1&key=
      Crawled 1 pages wit

      Crawled 1 pages with 1 transactions
    3130. Township: Taman Setia Permai - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Klang&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Setia%20Permai&page=1&key=
      Crawled 1 pages with 1 transactions
 Page 314 : https://www.edgeprop.my/jwdalice/api/v1/transactions/search?&category=RESIDENTIAL&state=SELANGOR&datefrom=2017-01-01&dateto=2019-12-31&page=314&respp=10&key=
   Page 314 of 317
    3131. Township: Taman Sri Antan - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Kajang&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Sri%20Antan&page=1&key=
      Crawled 1 pages with 1 transactions
    3132. Township: Taman Sri Banyan - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/

      Crawled 1 pages with 1 transactions
    3153. Township: Taman Yang Ming - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Batang%20Berjuntai&datefrom=2017-01-01&dateto=2019-12-31&project=Taman%20Yang%20Ming&page=1&key=
      Crawled 1 pages with 1 transactions
    3154. Township: Teluk Bunut - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Banting&datefrom=2017-01-01&dateto=2019-12-31&project=Teluk%20Bunut&page=1&key=
      Crawled 1 pages with 1 transactions
    3155. Township: TEMASYA 8 - Estimated 1 Transactions
     Date To: 2019-12-31 : https://www.edgeprop.my/jwdalice/api/v1/transactions/details?&category=RESIDENTIAL&state=SELANGOR&area=Shah%20Alam&datefrom=2017-01-01&dateto=2019-12-31&project=TEMASYA%208&page=1&key=
      Crawled 1 pages with 1 transactions
    

## Crawling POI Data from iProperty

In [7]:
# Function to crawl POI from iProperty

def crawl_poi(latitude, longitude, category=None):
    api = 'https://raptor.rea-asia.com/v1/graphql'

    headers = {
        'accept': '*/*',
        'accept-encoding': 'gzip, deflate, br',
        'accept-language': 'en-GB',
        'content-type': 'application/json',
        'market': 'MY',
        'origin': 'https://www.iproperty.com.my',
        'sec-fetch-mode': 'cors',
        'sec-fetch-site': 'cross-site',
        'user-agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/79.0.3945.130 Safari/537.36',
        'x-market': 'ipropertymy'
    }

    payload = {
        'operationName': None,
        'variables': {
            'lang': 'enGB',
            'location': str(latitude) + ',' + str(longitude),
            'radius': 5000,
            'pageSize': 100,
            'category': category
        },
        'query': 'query ($lang: AcceptLanguage, $location: String!, $radius: Int, $pageSize: Int, $category: PoiCategory) {\n  pois(location: $location, radius: $radius, pageSize: $pageSize, category: $category, lang: $lang) {\n    items {\n      name\n      subTypeLabel\n      subTypeExtra\n      geometry {\n        location {\n          lat\n          lng\n          __typename\n        }\n        __typename\n      }\n      subType\n      category\n      lineName\n      placeId\n      distance\n      distanceFloat\n      completionYear\n      type\n      city\n      district\n      publicType\n      curriculumOffered\n      __typename\n    }\n    __typename\n  }\n}\n'
    }

    retry_count = 0

    while True:
        retry_count = retry_count + 1
        if retry_count >= max_crawl_retry:
            return None

        try:
            request = requests.post(api, headers=headers, data=json.dumps(payload), timeout=30)
            request.raise_for_status()
            response = request.json()
        except requests.exceptions.HTTPError as errh:
            print('Http Error:', errh, '[Retry ' + str(retry_count) + ']')
        except requests.exceptions.ConnectionError as errc:
            print('Error Connecting:', errc, '[Retry ' + str(retry_count) + ']')
        except requests.exceptions.Timeout as errt:
            print('Timeout Error:', errt, '[Retry ' + str(retry_count) + ']')
        except requests.exceptions.RequestException as err:
            print('Unknown Error:', err, '[Retry ' + str(retry_count) + ']')
        else:
            return response


In [8]:
start_time = datetime.datetime.now()
print('Starts:', start_time)

# for each coordinate of the township recorded just now
for coordinate in coordinates:
    try:
        latitude = coordinate['latitude']
        longitude = coordinate['longitude']

        if pd.isna(latitude) or pd.isna(longitude):
            print('Skipped: Invalid GPS Coordinates', latitude, ',', longitude)
            continue

        poi_categories = ['education', 'healthcare', 'transportation']

        # crawl point of interest (POI) from iproperty
        print('Crawling POI near by', latitude, ',', longitude)
        for category in poi_categories:
            poi_list = list()
            response = crawl_poi(latitude, longitude, category)
            try:
                poi_list = poi_list + response['data']['pois']['items']
            except:
                e = str(sys.exc_info()[0]) + str(sys.exc_info()[1]) + str(sys.exc_info()[2])
                print('Error:', e)
                print('Error: Skipped and proceed for next POI category')
                continue

            with open(poi_data_directory + str(latitude) + '_' + str(longitude) + '_' + category + '.json', 'w') as json_file:
                json.dump(poi_list, json_file)

    except:
        e = str(sys.exc_info()[0]) + str(sys.exc_info()[1]) + str(sys.exc_info()[2])
        exc_type, exc_value, exc_traceback = sys.exc_info()
        print('Error:', e)
        print('Error: Failed to get listing information')
        traceback.print_exception(exc_type, exc_value, exc_traceback, limit=2, file=sys.stdout)

end_time = datetime.datetime.now()
print('Ends:', end_time)
print('Time Elapsed:', str(end_time - start_time))


Starts: 2020-06-10 04:07:13.584381
Crawling POI near by 2.4966866 , 102.8634842
Crawling POI near by 1.4807002 , 3.6579241
Crawling POI near by 1.502589941 , 103.9169998
Crawling POI near by 0 , 0
Crawling POI near by 1.493009 , 103.939636
Crawling POI near by 1.532019973 , 103.6220016
Crawling POI near by 1.523740053 , 103.6389999
Crawling POI near by 1.5063827 , 103.8744289
Crawling POI near by 0 , 0
Crawling POI near by 1.535629988 , 103.8010025
Crawling POI near by 0 , 0
Crawling POI near by 1.5522577 , 103.7603977
Crawling POI near by 1.5017922 , 103.8182753
Crawling POI near by 1.4603075 , 103.6514497
Crawling POI near by 1.5889063 , 103.8004903
Crawling POI near by 1.4778655 , 103.6779466
Crawling POI near by 1.519799948 , 103.6610031
Crawling POI near by 1.932752 , 102.9458774
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 1.542770028 , 103.7279968
Crawling POI near by 1.542449951 , 103.5810013
Crawling POI near by 1.6523929 , 103.5733333
Crawling PO

Crawling POI near by 1.4575789 , 103.5937719
Crawling POI near by None , None
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a6318748>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a6341108>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a6349f48>
Error: Skipped and proceed for next POI category
Crawling POI near by 1.496719956 , 103.9029999
Crawling POI near by 2.5274938 , 102.8041432
Crawling POI near by 1.8462884 , 103.6198597
Crawling POI near by None , None
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a633d048>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a1418a88>
Error: Skipped and proceed for next POI category
Er

Crawling POI near by 1.4899036 , 103.8140583
Crawling POI near by 1.492207 , 103.6534417
Crawling POI near by None , None
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1733e4f88>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a6344c48>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a1418a88>
Error: Skipped and proceed for next POI category
Crawling POI near by 1.512011 , 103.6830854
Crawling POI near by 0 , 0
Crawling POI near by 1.722406 , 103.892617
Crawling POI near by 1.4964844 , 103.8553677
Crawling POI near by 1.510750055 , 103.8249969
Crawling POI near by None , None
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a633d248>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' ob

Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a62ebf88>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a633db48>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1733e4f88>
Error: Skipped and proceed for next POI category
Crawling POI near by None , None
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a633cb08>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a633d7c8>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a62ebf88>
Error: Skipped and proceed for next POI category
Crawling POI near by 1.550938 , 103.79535
Crawling POI near by 1.48

Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a6344c48>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a62ebf88>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a1418a88>
Error: Skipped and proceed for next POI category
Crawling POI near by 2.0601172 , 102.6001773
Crawling POI near by 1.54432 , 103.7865987
Crawling POI near by 0 , 0
Crawling POI near by 1.8615621 , 102.9424615
Crawling POI near by 0 , 0
Crawling POI near by 1.603620052 , 103.8219986
Crawling POI near by 0 , 0
Crawling POI near by 1.518939972 , 103.8239975
Crawling POI near by None , None
Error: <class 'TypeError'>'NoneType' object is not subscriptable<traceback object at 0x7fe1a6318748>
Error: Skipped and proceed for next POI category
Error: <class 'TypeError'>'NoneType' object is not subscrip

...

Crawling POI near by 0 , 0
Crawling POI near by 3.208015 , 101.560471
Crawling POI near by 3.1732702 , 101.7361173
Crawling POI near by 2.9819465 , 101.5294282
Crawling POI near by 3.04009 , 101.4465464
Crawling POI near by 3.556501 , 101.6450362
Crawling POI near by 0 , 0
Crawling POI near by 3.041397 , 101.517491
Crawling POI near by 3.0446358 , 101.4345294
Crawling POI near by 3.6386708 , 101.5641815
Crawling POI near by 3.5155003 , 101.6480488
Crawling POI near by 2.7889107 , 101.7510846
Crawling POI near by 2.8013829 , 101.7496583
Crawling POI near by 2.7974371 , 101.7328387
Crawling POI near by 3.217676976 , 101.7630261
Crawling POI near by 2.97718 , 101.639
Crawling POI near by 3.02568 , 101.721001
Crawling POI near by 3.0785564 , 101.5458983
Crawling POI near by 2.924233 , 101.64753
Crawling POI near by 3.054619 , 101.605358
Crawling POI near by 3.03829 , 101.695
Crawling POI near by 3.235689 , 101.717783
Crawling POI near by 3.18982 , 101.594002
Crawling POI near by None , Non

Crawling POI near by 2.983735 , 101.640385
Crawling POI near by 3.03078 , 101.722351
Crawling POI near by 3.22952 , 101.716003
Crawling POI near by 3.5040236 , 101.1052519
Crawling POI near by 3.1739674 , 101.5843912
Crawling POI near by 3.2181054 , 101.750145
Crawling POI near by 0 , 0
Crawling POI near by 3.116862 , 101.770155
Crawling POI near by 3.217839 , 101.763523
Crawling POI near by 3.19397 , 101.605003
Crawling POI near by 3.090433 , 101.645645
Crawling POI near by 3.15087 , 101.587997
Crawling POI near by 3.3150128 , 101.4165255
Crawling POI near by 3.013991 , 101.698948
Crawling POI near by 3.022455 , 101.626274
Crawling POI near by 2.991877 , 101.804329
Crawling POI near by 0 , 0
Crawling POI near by 3.0324677 , 101.46567
Crawling POI near by 3.2369889 , 101.6738381
Crawling POI near by 3.1526 , 101.753998
Crawling POI near by 3.4175818 , 101.5856995
Crawling POI near by 0 , 0
Crawling POI near by 2.9634 , 101.730003
Crawling POI near by 2.8625037 , 101.6803594
Crawling PO

Crawling POI near by 3.133152 , 101.4402904
Crawling POI near by 3.0120358 , 101.8064555
Crawling POI near by 0 , 0
Crawling POI near by 3.0679286 , 101.4356427
Crawling POI near by 3.01708 , 101.702003
Crawling POI near by 0 , 0
Crawling POI near by 2.9897508 , 101.807954
Crawling POI near by 3.0178799 , 101.4832188
Crawling POI near by 3.7678804 , 100.9896076
Crawling POI near by 3.1913054 , 101.3121763
Crawling POI near by 2.637078 , 101.711322
Crawling POI near by 0 , 0
Crawling POI near by 3.0808962 , 101.7875192
Crawling POI near by 2.8374094 , 101.5252092
Crawling POI near by 0 , 0
Crawling POI near by 3.1160471 , 101.8242607
Crawling POI near by 0 , 0
Crawling POI near by 3.1441309 , 101.3766767
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 3.1462446 , 101.4281344
Crawling POI near by 3.1406103 , 101.3755428
Crawling POI near by 3.0550917 , 101.4564841
Crawling POI near by 3.26389 , 101.301422
Crawling POI near by 0 , 0
Cr

Crawling POI near by 0 , 0
Crawling POI near by 3.377959 , 101.3889064
Crawling POI near by 3.0343959 , 101.3990745
Crawling POI near by 3.7731651 , 100.9915272
Crawling POI near by 2.9428411 , 101.8390811
Crawling POI near by 0 , 0
Crawling POI near by 2.7967037 , 101.7232173
Crawling POI near by 3.1160557 , 101.8114365
Crawling POI near by 3.3431822 , 101.5555083
Crawling POI near by 3.326065 , 101.571459
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 3.13771 , 101.775002
Crawling POI near by 2.9805831 , 101.788511
Crawling POI near by 3.17996 , 101.760002
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 2.8603704 , 101.6709169
Crawling POI near by 2.8882922 , 101.7151178
Crawling POI near by 0 , 0
Crawling POI near by 3.13709 , 101.378165
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 0 , 0
Crawling POI near by 3.0284331 , 101.7731085
Crawling POI near by 3.0482824 , 101.7904

Crawling POI near by 0 , 0
Crawling POI near by 3.1261371 , 101.5734222
Crawling POI near by 0 , 0
Crawling POI near by 3.04787 , 101.764
Crawling POI near by 3.1247 , 101.784993
Crawling POI near by 3.0395045 , 101.7880978
Crawling POI near by 3.1898027 , 101.7637585
Crawling POI near by 3.2229758 , 101.7098828
Crawling POI near by 2.91928 , 101.654999
Crawling POI near by 3.074707 , 101.4983474
Crawling POI near by 2.9230104 , 101.7264277
Crawling POI near by 3.16925 , 101.757004
Crawling POI near by 3.19971 , 101.778
Crawling POI near by 2.97883 , 101.783997
Crawling POI near by 0 , 0
Crawling POI near by 3.214352 , 101.470651
Crawling POI near by 0 , 0
Crawling POI near by 3.288877 , 101.469828
Crawling POI near by 0 , 0
Crawling POI near by 3.23638 , 101.65126
Crawling POI near by 3.262523 , 101.647166
Crawling POI near by 3.2253419 , 101.4472423
Crawling POI near by 2.9834609 , 101.6620711
Crawling POI near by 3.098693 , 101.76477
Crawling POI near by 3.10251 , 101.599998
Crawlin